In [11]:
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd

import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas_profiling as pp

%matplotlib inline

In [2]:
data = pd.read_csv("Company_Data.csv")
print(data.columns)
data.head()

Index(['Sales', 'CompPrice', 'Income', 'Advertising', 'Population', 'Price',
       'ShelveLoc', 'Age', 'Education', 'Urban', 'US'],
      dtype='object')


Sales  CompPrice  Income  Advertising  Population  Price ShelveLoc  Age  \
0   9.50        138      73           11         276    120       Bad   42   
1  11.22        111      48           16         260     83      Good   65   
2  10.06        113      35           10         269     80    Medium   59   
3   7.40        117     100            4         466     97    Medium   55   
4   4.15        141      64            3         340    128       Bad   38   

   Education Urban   US  
0         17   Yes  Yes  
1         10   Yes  Yes  
2         12   Yes  Yes  
3         14   Yes  Yes  
4         13   Yes   No

In [3]:
pd.set_option("display.float_format", "{:.2f}".format)
data.describe()

Sales  CompPrice  Income  Advertising  Population  Price    Age  \
count 400.00     400.00  400.00       400.00      400.00 400.00 400.00   
mean    7.50     124.97   68.66         6.63      264.84 115.80  53.32   
std     2.82      15.33   27.99         6.65      147.38  23.68  16.20   
min     0.00      77.00   21.00         0.00       10.00  24.00  25.00   
25%     5.39     115.00   42.75         0.00      139.00 100.00  39.75   
50%     7.49     125.00   69.00         5.00      272.00 117.00  54.50   
75%     9.32     135.00   91.00        12.00      398.50 131.00  66.00   
max    16.27     175.00  120.00        29.00      509.00 191.00  80.00   

       Education  
count     400.00  
mean       13.90  
std         2.62  
min        10.00  
25%        12.00  
50%        14.00  
75%        16.00  
max        18.00

In [4]:
data.drop(['Sales'], axis="columns", inplace=True)

In [5]:
categorical_col = []
for column in data.columns:
    if data[column].dtype == object and len(data[column].unique()) <= 50:
        categorical_col.append(column)
        print(f"{column} : {data[column].unique()}")
        print("====================================")

ShelveLoc : ['Bad' 'Good' 'Medium']
Urban : ['Yes' 'No']
US : ['Yes' 'No']


In [8]:
data['ShelveLoc'] = data.ShelveLoc.astype("category").cat.codes
data['Urban'] = data.Urban.astype("category").cat.codes
data['US'] = data.US.astype("category").cat.codes

In [9]:
data

CompPrice  Income  Advertising  Population  Price  ShelveLoc  Age  \
0          138      73           11         276    120          0   42   
1          111      48           16         260     83          1   65   
2          113      35           10         269     80          2   59   
3          117     100            4         466     97          2   55   
4          141      64            3         340    128          0   38   
..         ...     ...          ...         ...    ...        ...  ...   
395        138     108           17         203    128          1   33   
396        139      23            3          37    120          2   55   
397        162      26           12         368    159          2   40   
398        100      79            7         284     95          0   50   
399        134      37            0          27    120          1   49   

     Education  Urban  US  
0           17      1   1  
1           10      1   1  
2           12      1   1  
3           14      1   1  
4           13      1   0  
..         ...    ...  ..  
395         14      1   1  
396         11      0   1  
397         18      1   1  
398         12      1   1  
399         16      1   1  

[400 rows x 10 columns]

In [13]:
EDA_Report=pp.ProfileReport(data)
EDA_Report

In [14]:
from sklearn.preprocessing import LabelEncoder

label = LabelEncoder()
for column in categorical_col:
    data[column] = label.fit_transform(data[column])

In [15]:
from sklearn.model_selection import train_test_split

X = data.drop('ShelveLoc', axis=1)
y = data.ShelveLoc

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)


In [16]:
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report

def print_score(clf, X_train, y_train, X_test, y_test, train=True):
    if train:
        pred = clf.predict(X_train)
        clf_report = pd.DataFrame(classification_report(y_train, pred, output_dict=True))
        print("Train Result:\n================================================")
        print(f"Accuracy Score: {accuracy_score(y_train, pred) * 100:.2f}%")
        print("_______________________________________________")
        print(f"CLASSIFICATION REPORT:\n{clf_report}")
        print("_______________________________________________")
        print(f"Confusion Matrix: \n {confusion_matrix(y_train, pred)}\n")
        
    elif train==False:
        pred = clf.predict(X_test)
        clf_report = pd.DataFrame(classification_report(y_test, pred, output_dict=True))
        print("Test Result:\n================================================")        
        print(f"Accuracy Score: {accuracy_score(y_test, pred) * 100:.2f}%")
        print("_______________________________________________")
        print(f"CLASSIFICATION REPORT:\n{clf_report}")
        print("_______________________________________________")
        print(f"Confusion Matrix: \n {confusion_matrix(y_test, pred)}\n")

In [17]:
from sklearn.tree import DecisionTreeClassifier

tree_clf = DecisionTreeClassifier(random_state=42)
tree_clf.fit(X_train, y_train)

print_score(tree_clf, X_train, y_train, X_test, y_test, train=True)
print_score(tree_clf, X_train, y_train, X_test, y_test, train=False)

Train Result:
Accuracy Score: 100.00%
_______________________________________________
CLASSIFICATION REPORT:
              0     1      2  accuracy  macro avg  weighted avg
precision  1.00  1.00   1.00      1.00       1.00          1.00
recall     1.00  1.00   1.00      1.00       1.00          1.00
f1-score   1.00  1.00   1.00      1.00       1.00          1.00
support   68.00 56.00 156.00      1.00     280.00        280.00
_______________________________________________
Confusion Matrix: 
 [[ 68   0   0]
 [  0  56   0]
 [  0   0 156]]

Test Result:
Accuracy Score: 35.83%
_______________________________________________
CLASSIFICATION REPORT:
              0     1     2  accuracy  macro avg  weighted avg
precision  0.08  0.10  0.51      0.36       0.23          0.31
recall     0.07  0.07  0.62      0.36       0.25          0.36
f1-score   0.08  0.08  0.56      0.36       0.24          0.33
support   28.00 29.00 63.00      0.36     120.00        120.00
__________________________________

In [18]:
from sklearn.ensemble import RandomForestClassifier

rf_clf = RandomForestClassifier(n_estimators=100)
rf_clf.fit(X_train, y_train)

print_score(rf_clf, X_train, y_train, X_test, y_test, train=True)
print_score(rf_clf, X_train, y_train, X_test, y_test, train=False)

Train Result:
Accuracy Score: 100.00%
_______________________________________________
CLASSIFICATION REPORT:
              0     1      2  accuracy  macro avg  weighted avg
precision  1.00  1.00   1.00      1.00       1.00          1.00
recall     1.00  1.00   1.00      1.00       1.00          1.00
f1-score   1.00  1.00   1.00      1.00       1.00          1.00
support   68.00 56.00 156.00      1.00     280.00        280.00
_______________________________________________
Confusion Matrix: 
 [[ 68   0   0]
 [  0  56   0]
 [  0   0 156]]

Test Result:
Accuracy Score: 49.17%
_______________________________________________
CLASSIFICATION REPORT:
              0     1     2  accuracy  macro avg  weighted avg
precision  0.00  0.00  0.52      0.49       0.17          0.27
recall     0.00  0.00  0.94      0.49       0.31          0.49
f1-score   0.00  0.00  0.67      0.49       0.22          0.35
support   28.00 29.00 63.00      0.49     120.00        120.00
__________________________________